# Overview 
- In this task you work with a data set of used cars scraped in October 2025 from Autoscout24.
- **Today's task** is to start with a visual exploratory data analysis of the data set. 
- In the **next class**, you will pick a few selected visualizations from today's analysis, and finetune them according to the best practices discussed in class. 
- Many of the variables should be self-explanatory. For others you may check how the data is represented on the Autoscout24 website (e.g. [here](https://www.autoscout24.de/angebote/volkswagen-caddy-caddy-1-2tsi-trendline-benzin-schwarz-77ba4423-1129-497b-bf33-30b978391040)). Or feel free to ask me directly.

# Today's task

- Your goal is to create a series of visualizations that gives first insights into the data. 
- Check Plotly's [gallery on basic charts](https://plotly.com/python/basic-charts/) to get started. Start simple!
- Reflect:
    * Do you observe interesting patterns?
    * Why or why not? What are the limitations of the plots? How could you improve them in the next step?
- Try to cover different types of aspects such as: 
    * **Relationships** between different numerical variables
    * **Differences** between groups (e.g. brands, fuel types, etc.)
    * **Changes over time** (Note: all data is from October 2025, but you can inspect the age of the cars)
    * **Geographical patterns**


# Visual EDA

In [1]:
import pandas as pd 
import plotly.express as px

In [2]:
df = pd.read_csv("used_cars.csv")
df.head(3)

make   model                                  subtitle  zip_code  \
0  volkswagen  amarok       3.0 TDI Aventura 4Motion MATRIX-LED     25337   
1  volkswagen  amarok  Life DC 2.0 TDI 4Motion AUT LED AHK Navi     22761   
2  volkswagen  amarok                   Life DC 2.0 TDI 4Motion     24941   

   longitude  latitude  price                body_type fuel_type  power  ...  \
0    9.69682  53.74876  44900  SUV/Geländewagen/Pickup    Diesel  177.0  ...   
1    9.89825  53.56986  43889                   Allrad    Diesel  151.0  ...   
2    9.42538  54.76741  48890  SUV/Geländewagen/Pickup    Diesel  151.0  ...   

  environment_badge  exterior_color  exterior_color_detail  interior_color  \
0          4 (Grün)           Black         Midnight black           Black   
1               NaN        Metallic                Schwarz    Keine Angabe   
2          4 (Grün)           White            Clear White           Black   

   seats price_label  seller_type  boost_level  relevance_adjustment  position  
0    5.0  good-price   Commercial          t40                 boost       291  
1    NaN  good-price   Commercial          t40                 boost       363  
2    5.0  fair-price   Commercial          t50                 boost       182  

[3 rows x 30 columns]

In [78]:
df.columns

Index(['make', 'model', 'subtitle', 'zip_code', 'longitude', 'latitude',
       'price', 'body_type', 'fuel_type', 'power', 'gearbox', 'age', 'mileage',
       'fahrzeughalter', 'service_book', 'smoke_free', 'cylinders',
       'engine_size', 'weight', 'co2_emissions', 'environment_badge',
       'exterior_color', 'exterior_color_detail', 'interior_color', 'seats',
       'price_label', 'seller_type', 'boost_level', 'relevance_adjustment',
       'position', 'mileage_bin'],
      dtype='object')

In [47]:
px.scatter(df, x="age", y ="mileage", color="price")

In [82]:
fig = px.scatter(df, x="longitude", y ="latitude", color="zip_code")
fig.update_layout(width=800, height=800)

In [ ]:
# price is less than 50k
# mileage less than 500k
df_price = df[df["price"] < 50000]
df_price = df_price[df_price["mileage"] < 500000]

In [34]:
px.scatter(df_price, x="age", y ="mileage", color="price")

In [33]:
fig = px.scatter(df_price, x="longitude", y ="latitude", color="mileage")
fig.update_layout(width=800, height=800)

In [23]:
fuel_counts = df['fuel_type'].value_counts()
px.pie(values=fuel_counts.values, names=fuel_counts.index, title='Fuel Type Distribution')

In [41]:
bins = [0, 20000, 40000, 60000, 80000, 100000, 150000, 200000, 300000]
labels = ["0–20k", "20–40k", "40–60k", "60–80k", "80–100k",
          "100–150k", "150–200k", "200–300k"]

df["mileage_bin"] = pd.cut(df["mileage"], bins=bins, labels=labels)

count_per_bin = df["mileage_bin"].value_counts().sort_index()

px.bar(
    x=count_per_bin.index,
    y=count_per_bin.values,
    labels={"x": "Mileage Range", "y": "Count"},
    title="Mileage Distribution"
)


In [46]:
df_mile = df[df["mileage"] < 250000]
px.histogram(
    df_mile,
    x="mileage",
    color='fuel_type',
    nbins=25,
    title="Mileage Histogram"
)

In [81]:
fig = px.box(
    df,
    x="make",      # replace with your brand column name
    y="price",      # replace with your price column name
    title="Price Distribution by Car Brand",
    labels={"brand": "Car Brand", "price": "Price (€)"}
)

fig.update_layout(xaxis_tickangle=-45,
                  width=1200, height=600)  
fig.update_yaxes(range=[0, 100000]) 
#fig.update_yaxes(type="log")
fig.show()

In [68]:
mean_prices = df.groupby('make')['price'].mean().reset_index()
px.bar(
    mean_prices,
    x='make',
    y='price',
    title='Mean Price per Car Brand',
    labels={'brand': 'Car Brand', 'price': 'Mean Price (€)'}
)

In [70]:
summary = df.groupby('make')['price'].agg(['mean', 'count']).reset_index()

# Sort by mean price for nicer order (optional)
summary = summary.sort_values('mean', ascending=False)

# Scatter plot with bubble size = count
fig = px.scatter(
    summary,
    x='make',
    y='mean',
    size='count',
    size_max=60,  # max bubble size
    title='Mean Price per Brand with Number of Cars',
    labels={'make': 'Car Brand', 'mean': 'Mean Price (€)', 'count': 'Number of Cars'},
    hover_name='make',
)

fig.update_layout(xaxis_tickangle=-45)  # Rotate labels for readability

fig.show()

In [72]:
# Group by brand and fuel type, calculate mean price and mean mileage
summary = df.groupby(['make', 'fuel_type']).agg({
    'price': 'mean',
    'mileage': 'mean',
    'fuel_type': 'count'  # just to check counts if needed
}).rename(columns={'fuel_type': 'count'}).reset_index()

fig = px.scatter(
    summary,
    x='make',
    y='fuel_type',
    size='price',           # bubble size = avg price
    color='mileage',        # color by avg mileage
    color_continuous_scale='Viridis',
    size_max=60,
    title='Average Price and Mileage by Brand and Fuel Type',
    labels={
        'make': 'Car Brand',
        'fuel_type': 'Fuel Type',
        'price': 'Average Price (€)',
        'mileage': 'Average Mileage (km)'
    },
    hover_data={'count': True, 'price': ':.2f', 'mileage': ':.0f'}
)

fig.update_layout(xaxis_tickangle=-45)

fig.show()


In [74]:
# Count number of cars per brand and fuel type
summary = df.groupby(['make', 'fuel_type']).size().reset_index(name='count')

px.scatter(
    summary,
    x='make',
    y='fuel_type',
    size='count',       # bubble size = count of cars
    size_max=60,
    title='Number of Cars per Brand and Fuel Type',
    labels={'make': 'Car Brand', 'fuel_type': 'Fuel Type', 'count': 'Number of Cars'},
    hover_name='make'
)

In [76]:
# Set the fuel type you want to filter by
selected_fuel = "Hydrogen"  # change this to any fuel type you want

# Filter dataframe
filtered_df = df[df['fuel_type'] == selected_fuel]

# Count number of cars per brand for the selected fuel type
brand_counts = filtered_df['make'].value_counts().reset_index()
brand_counts.columns = ['make', 'count']

fig = px.bar(
    brand_counts,
    x='make',
    y='count',
    title=f'Number of {selected_fuel} Cars per Brand',
    labels={'make': 'Car Brand', 'count': 'Number of Cars'}
)

fig.update_layout(xaxis_tickangle=-45)

fig.show()


In [77]:
px.sunburst(
    df,
    path=['fuel_type', 'make'],  # hierarchy: fuel type → brand
    values=None,                  # size by count automatically
    title='Car Distribution by Fuel Type and Brand'
)